# Math 124 - Programming for Mathematical Applications
Per-Olof Persson, UC Berkeley

## Project 4 - Image Segmentation

### Description

*Image segmentation* is a technique for partitioning an image into multiple segments (regions), in order to identify objects and boundaries. This is a fundamental task in computer vision with a wide range of applications, including medical imaging (e.g., finding tumors), autonomous driving (e.g., identifying pedestrians and roads), and satellite imagery analysis.

In this project, you will implement a popular segmentation technique based on **morphological image processing**. This is a classic and robust method that uses small "kernels" or "stencils" to modify the shape and structure of features within an image. We will first build fundamental stencils for operations like **Erosion** and **Dilation**. Then, we will combine these building blocks to create a simple, fast, and effective program for cleaning a noisy image and successfully segmenting its objects.

### Preliminaries: Helper Functions and Test Images

First, we'll set up the tools we need. We'll define some of the functions from the course notes, and a function `test_image` to create sample images for testing our algorithm.

In [ ]:
using Plots
Base.showable(::MIME"image/svg+xml", ::Plots.Plot) = false  # Disable SVG
toRGBarray(img) = RGB.(eachslice(img[:,:,:], dims=3)...)
imshow(img; args...) = plot(toRGBarray(img); aspect_ratio=:equal, axis=nothing, border=:none, args...)

function test_image(imgcase, m=50, noise=0)
    A = 0.8*ones(Float64, m, m)
    if imgcase == 1
        i = 1:m
        sc = m/100
        for c in [[50,60,20], [65,60,15], [35,30,15]]
            A = @. max(0.2, A - 0.6*Float64((i - sc*c[1])^2 + 
                    (i' - sc*c[2])^2 < (sc*c[3])^2))
        end
    elseif imgcase == 2
        is = [[25,35,25,35], [65,75,65,75], [65,75,45,50], [40,45,40,70]]
        for i in is
            i = round.(Int, i*m/100)
            A[i[1]:i[2], i[3]:i[4]] .= 0.3
        end
    else
        error("Unknown image case")
    end
    
    A += noise*randn(size(A))
    A = min.(max.(A, 0), 1)
end

### The `Stencil` Abstract Type

A "stencil" is a powerful concept in scientific computing. It represents a recurring computational pattern applied to a small neighborhood of points in a grid. A common example is a 3x3 stencil, which computes a new value for a pixel based on itself and its 8 immediate neighbors.

We will define an *abstract type*, `AbstractStencil`, to create a common interface for all our stencils. We'll also define a function `apply_to_3x3` which will be the *only* function we need to implement for each new *concrete* stencil type. This is a very flexible and Julian design pattern.

In [ ]:
# Define the abstract supertype for all our stencils
abstract type AbstractStencil end

# Define the function that each concrete stencil must implement.
# It takes a stencil 's' and a 3x3 matrix 'A' and returns a single number.
function apply_to_3x3(s::AbstractStencil, A)
    # This is a placeholder. If a subtype doesn't implement this, Julia will throw an error.
    error("apply_to_3x3 not implemented for $(typeof(s))")
end

### Problem 1 - Stencils

Now we'll create the main function to apply any stencil to a full image, and then define a few specific stencils.

#### Problem 1(a): Implementing `apply_stencil` with Boundary Handling

Your first task is to complete the `apply_stencil(s, A)` function. This function will take a stencil `s` and an image `A` (as a matrix) and return a new image `B` of the same size.

The main idea is to loop through each pixel `(i, j)` of the input image `A`. The corresponding value in the new image, `B[i, j]`, will be calculated by calling `apply_to_3x3(s, patch)`, where `patch` is the 3x3 neighborhood of pixels in `A` centered at `(i, j)`.

**The Boundary Problem:**

For an "interior" pixel (one not on the edge), its 3x3 neighborhood `A[i-1:i+1, j-1:j+1]` is straightforward to get. But what about a pixel on the border, like `(1, 1)`? The neighborhood `A[0:2, 0:2]` would try to access indices like `A[0, 1]` or `A[1, 0]`, which are outside the array and would cause an error.

**Our Solution: Replication (Clamping)**

We will solve this by "replicating" the edge pixels. This means any time the stencil tries to "look outside the image," we'll simply use the value of the **closest pixel that is inside** the image.

* A request for `A[0, j]` (which is out-of-bounds) will be "clamped" and will use `A[1, j]` instead.
* A request for `A[i, 0]` will use `A[i, 1]`.
* If the image has `m` rows, a request for `A[m+1, j]` will use `A[m, j]`.

**Hint:** The Julia function `clamp(value, lo, hi)` is the perfect tool for this. It takes a `value` and "clamps" it to the range `[lo, hi]`, ensuring the result is never smaller than `lo` or larger than `hi`. Your goal is to use this to build the 3x3 patch for *every* pixel. This approach is powerful because you can use the same clean logic for both interior pixels and boundary pixels without needing separate `if` statements.

In [ ]:
function apply_stencil(s::AbstractStencil, A)
    # TODO: Complete the implementation of the function
end

#### Problem 1(b): The Identity Stencil

The code below defines a concrete type `IdentityStencil <: AbstractStencil`. Fill in the definition of its corresponding `apply_to_3x3` method. This stencil should do nothing: the output `B[i,j]` should simply be the original value `A[i,j]`. 

This is a crucial "unit test" for our `apply_stencil` function. If it works, we know the looping and boundary handling logic is correct.

In [ ]:
# Define the empty struct. It's just a "tag" to tell Julia which method to use.
struct IdentityStencil <: AbstractStencil end

# TODO: Complete the definition of the function `apply_to_3x3' method for the identity.
apply_to_3x3(s::IdentityStencil, A) = # TODO

In [ ]:
# Test code for 1(b)
m = 10
A = randn(m,m) # Create a random 10x10 test image
B = apply_stencil(IdentityStencil(), A)

# Check if the input and output are identical
println("Identity test passed: ", A == B)

#### Problem 1(c): The Averaging Stencil (Box Blur)

Define the new concrete type `AvgStencil <: AbstractStencil`. This stencil should compute the average (mean) of all 9 pixels in the 3x3 neighborhood. This is also known as a "box blur," and its effect is to smooth or blur the image, reducing noise and sharp details.

In [ ]:
# Test code for 1(c)
A = test_image(1, 100, 0.3) # Create a 100x100 image with noise
B = apply_stencil(AvgStencil(), A)

# Plot the original and blurred images side-by-side
plot(imshow(A, title="Original with Noise"), imshow(B, title="Averaged (Blurred)"),
     titlefontsize=10, size=(600,300))

#### Problem 1(d): The Laplacian Stencil

Define the new concrete type `LaplaceStencil <: AbstractStencil`. This stencil should compute the 5-point discrete Laplacian, a fundamental operation in image processing and numerical PDEs. 

The formula is: $L(A) = 4A_{i,j} - A_{i-1,j} - A_{i+1,j} - A_{i,j-1} - A_{i,j+1}$

This operator approximates the second derivative of the image intensity. It measures the "curvature" of the image and is very large at edges or sharp features, making it excellent for edge detection.

In [ ]:
# Test code for 1(d)
A = test_image(1, 100) # Use the clean image for better edge visibility
B = apply_stencil(LaplaceStencil(), A)

# Plot the original and the Laplacian
# Note: The Laplacian image will look mostly gray, with bright/dark lines at the edges.
plot(imshow(A, title="Original"), imshow(B, title="Laplacian (Edges)"),
     titlefontsize=10, size=(600,300))

### Problem 2 - Morphological Stencils

A faster and robust approach to image cleaning and segmentation is based on **morphological operations**. These operations use stencils to modify the *shape* (or morphology) of features in an image based on a 3x3 neighborhood. The two fundamental operations are **Erosion** and **Dilation**.

#### Problem 2(a): The `ErodeStencil`

Define a concrete type `ErodeStencil <: AbstractStencil` and its corresponding `apply_to_3x3` method. 

This stencil's operation is simple: it finds and returns the **minimum** value of all 9 pixels in the 3x3 neighborhood.

This operation has the effect of "eroding" or shrinking the boundaries of bright regions. It is also extremely effective at removing small, bright noise (often called "salt" noise).

#### Problem 2(b): The `DilateStencil`

Define `DilateStencil <: AbstractStencil`. This stencil is the opposite of erosion: it finds and returns the **maximum** value of all 9 pixels in the 3x3 neighborhood.

This operation has the effect of "dilating" or growing the boundaries of bright regions. It is good for filling in small, dark holes (often called "pepper" noise).

In [ ]:
# Test code for 2(a) and 2(b)
plts = []
for imgcase = 1:2
    # Create the noisy image
    A = test_image(imgcase, 100, 0.3)

    # Apply the new stencils
    B_eroded = apply_stencil(ErodeStencil(), A)
    B_dilated = apply_stencil(DilateStencil(), A)
    
    # --- Plot all the steps --- 
    push!(plts, imshow(A, title="Original with Noise"))
    push!(plts, imshow(B_eroded, title="Eroded"))
    push!(plts, imshow(B_dilated, title="Dilated"))
end
plot(plts..., titlefontsize=10, size=(800,600))

### Problem 3 - Image Cleaning and Segmentation

Now we can combine these simple stencils into powerful, standard operations for "cleaning" an image, which makes segmentation much easier and more reliable.

#### Problem 3(a): The "Opening" Operation

An **"Opening"** operation is one of the most useful tools in image cleaning. It's defined as a morphological **Erosion followed by a Dilation**.

Its power comes from this sequence:
1.  The **Erosion** pass removes small, bright noise (like the "salt" in our noisy image).
2.  The **Dilation** pass then restores the size of the *main, larger* objects that survived the erosion.

Implement a function `image_open(A)` that takes an image `A` and returns the result of this two-step process.

#### Problem 3(b): Segmentation via Cleaning and Thresholding

Now, let's put everything together to create a robust segmentation pipeline that is much simpler and faster than the level-set method.

Your task is to:
1.  Create a noisy `test_image(imgcase, 100, 0.3)` where `imgcase` looping over `1` and `2`.
2.  Apply the `AvgStencil` (from Problem 1) to blur the image slightly. This helps to smooth out the noise and average the intensities.
3.  Apply your new `image_open` function (from 3a) to the blurred image. This will remove most of the remaining noise "islands."
4.  Apply a simple, hard threshold to segment the cleaned image (similar to the example in the course notes). Our original image from `test_image` has background=0 and objects=1. After blurring and cleaning, a threshold of `0.5` is a good choice to separate the objects from the background.

This final image is your segmentation! Plot the original, the cleaned intermediate, and the final segmented image, for both `imgcase=1` and `2` (a total of six plots).